In [1]:
try:
    import google.colab  # noqa: F401

    # specify the version of DataEval (==X.XX.X) for versions other than the latest
    %pip install -q dataeval maite-datasets
except Exception:
    pass

In [2]:
import numpy as np
import polars as pl
from maite_datasets.object_detection import VOCDetection

from dataeval import Metadata

# Load the classes from DataEval that are helpful for EDA
from dataeval.config import set_max_processes
from dataeval.core import calculate, label_stats
from dataeval.core.flags import ImageStats
from dataeval.quality import Duplicates, Outliers

# Print all rows of dataframes
_ = pl.Config.set_tbl_rows(-1)

# Set the random value
rng = np.random.default_rng(213)

# Set multiprocessing for DataEval stats
set_max_processes(4)

In [3]:
# Helper method to plot sample images by class
def plot_sample_images_by_class(dataset, image_indices_per_class) -> None:
    import matplotlib.pyplot as plt

    # Plot random images from each category
    _, axs = plt.subplots(5, 4, figsize=(8, 10))

    for ax, (category, indices) in zip(axs.flat, image_indices_per_class.items()):
        # Randomly select an index from the list of indices
        ax.imshow(dataset[rng.choice(indices)][0].transpose(1, 2, 0))
        ax.set_title(dataset.metadata["index2label"][category])
        ax.axis("off")

    plt.tight_layout()
    plt.show()


# Helper method to plot images of interest
def plot_sample_outlier_images_by_metric(dataset, outlier_class, outlier_result, metric, layout) -> None:
    import matplotlib.pyplot as plt
    from matplotlib.cm import ScalarMappable
    from matplotlib.colors import Normalize

    # Filter issues DataFrame for the specific metric
    metric_issues = outlier_result.issues.filter(pl.col("metric_name") == metric)
    image_ids = metric_issues["item_id"].unique().to_list()

    if not image_ids:
        print(f"No images flagged for metric: {metric}")
        return

    # Get all metric values for the entire dataset to understand the distribution
    all_metric_values = outlier_class.stats["stats"][metric]
    quantiles = np.quantile(all_metric_values, [0, 0.25, 0.5, 0.75, 1])
    median = quantiles[2]

    # Calculate distance from median for each flagged image and sort by distance (descending)
    metric_values_with_ids = []
    for img_id in image_ids:
        metric_value = metric_issues.filter(pl.col("item_id") == img_id)["metric_value"][0]
        distance_from_median = abs(metric_value - median)
        metric_values_with_ids.append((img_id, metric_value, distance_from_median))

    # Sort by distance from median (most outlier first)
    metric_values_with_ids.sort(key=lambda x: x[2], reverse=True)

    # Create figure with space for colorbar
    fig = plt.figure(figsize=(12, layout[0] * 4))

    # Create grid spec with extra space for colorbar
    import matplotlib.gridspec as gridspec

    gs = gridspec.GridSpec(
        layout[0],
        layout[1] + 1,
        width_ratios=[1] * layout[1] + [0.05],
        hspace=0.4,
        wspace=0.1,
        left=0.05,
        right=0.92,
        top=0.96,
        bottom=0.02,
    )

    # Determine number of samples to plot
    n_samples = min(int(np.prod(layout)), len(image_ids))

    # Create colormap normalization based on full metric distribution
    vmin, vmax = quantiles[0], quantiles[4]
    norm = Normalize(vmin=vmin, vmax=vmax)
    cmap = plt.get_cmap("viridis")

    # Plot images
    for i in range(n_samples):
        row = i // layout[1]
        col = i % layout[1]
        ax = fig.add_subplot(gs[row, col])

        img_id, metric_value, _ = metric_values_with_ids[i]

        # Get color for this metric value
        color = cmap(norm(metric_value))

        # Plot image
        ax.imshow(dataset[img_id][0].transpose(1, 2, 0))

        # Place metric details as footer below the image using xlabel (black text for legibility)
        ax.set_xlabel(f"index: {img_id}\n{metric}: {np.round(metric_value, 3)}", fontsize=9, color="black")

        # Turn off ticks but keep spines for colored border
        ax.set_xticks([])
        ax.set_yticks([])

        # Add 5-pixel colored border to indicate extremeness
        for spine in ax.spines.values():
            spine.set_edgecolor(color)
            spine.set_linewidth(5)
            spine.set_visible(True)

    # Add colorbar with quantile markers
    cbar_ax = fig.add_subplot(gs[:, -1])
    sm = ScalarMappable(cmap=cmap, norm=norm)
    sm.set_array([])
    cbar = plt.colorbar(sm, cax=cbar_ax)
    cbar.set_ticks([])

    # Add quantile markers on colorbar
    quantile_labels = ["Min (Q0)", "Q1 (25%)", "Median (Q2)", "Q3 (75%)", "Max (Q4)"]
    for q_val, q_label in zip(quantiles, quantile_labels):
        cbar.ax.axhline(q_val, color="black", linestyle="--", linewidth=0.8, alpha=0.7)
        cbar.ax.text(
            1.5,
            q_val,
            f"{q_label}\n{np.round(q_val, 2)}",
            va="center",
            fontsize=8,
            transform=cbar.ax.get_yaxis_transform(),
        )

    # Add overall title with more top space
    fig.suptitle(f'Outlier Images for "{metric}" (sorted by distance from median)', fontsize=12, y=0.99)

    plt.show()

In [4]:
# Download the data and then load it as a torch Tensor
ds = VOCDetection("./data", image_set="train", year="2012", download=True)
print(ds)

VOCDetection Dataset
--------------------
    Year: 2012
    Transforms: []
    Image Set: train
    Metadata: {'id': 'VOCDetection_train', 'index2label': {0: 'aeroplane', 1: 'bicycle', 2: 'bird', 3: 'boat', 4: 'bottle', 5: 'bus', 6: 'car', 7: 'cat', 8: 'chair', 9: 'cow', 10: 'diningtable', 11: 'dog', 12: 'horse', 13: 'motorbike', 14: 'person', 15: 'pottedplant', 16: 'sheep', 17: 'sofa', 18: 'train', 19: 'tvmonitor'}, 'split': 'train'}
    Path: /builds/jatic/aria/dataeval/docs/source/notebooks/data/vocdataset/VOCdevkit/VOC2012
    Size: 5717


In [5]:
# Calculate basic label statistics from the dataset
lstats = label_stats(((lbl for lbl in d[1].labels) for d in ds), ds.index2label)

# View per_class data as a DataFrame
pl.DataFrame(
    {
        "class_name": list(ds.index2label.values()),
        "label_count": [lstats["label_counts_per_class"][k] for k in ds.index2label],
        "image_count": [lstats["image_counts_per_class"][k] for k in ds.index2label],
    }
)

shape: (20, 3)
┌─────────────┬─────────────┬─────────────┐
│ class_name  ┆ label_count ┆ image_count │
│ ---         ┆ ---         ┆ ---         │
│ str         ┆ i64         ┆ i64         │
╞═════════════╪═════════════╪═════════════╡
│ aeroplane   ┆ 470         ┆ 328         │
│ bicycle     ┆ 410         ┆ 281         │
│ bird        ┆ 592         ┆ 399         │
│ boat        ┆ 508         ┆ 264         │
│ bottle      ┆ 749         ┆ 399         │
│ bus         ┆ 317         ┆ 219         │
│ car         ┆ 1191        ┆ 621         │
│ cat         ┆ 609         ┆ 540         │
│ chair       ┆ 1457        ┆ 656         │
│ cow         ┆ 355         ┆ 155         │
│ diningtable ┆ 373         ┆ 318         │
│ dog         ┆ 768         ┆ 636         │
│ horse       ┆ 377         ┆ 238         │
│ motorbike   ┆ 375         ┆ 274         │
│ person      ┆ 5019        ┆ 2142        │
│ pottedplant ┆ 557         ┆ 289         │
│ sheep       ┆ 509         ┆ 171         │
│ sofa        ┆ 399         ┆ 359         │
│ train       ┆ 327         ┆ 275         │
│ tvmonitor   ┆ 412         ┆ 299         │
└─────────────┴─────────────┴─────────────┘

In [6]:
plot_sample_images_by_class(ds, lstats["image_indices_per_class"])

In [7]:
# This cell takes about 1-5 minutes to run depending on your hardware

# Initialize the Outliers class
outliers = Outliers(outlier_method="zscore")

# Find the extreme images
outlier_imgs = outliers.evaluate(ds)

# View the number of extreme images
print(f"Number of images with extreme values: {len(outlier_imgs)}")

/builds/jatic/aria/dataeval/src/dataeval/core/_calculate.py:355: RuntimeWarning: overflow encountered in cast
  np_array = np_array.astype(np.float16)


Number of images with extreme values: 1172


/builds/jatic/aria/dataeval/.nox/docs/lib/python3.13/site-packages/numpy/lib/_nanfunctions_impl.py:1867: RuntimeWarning: invalid value encountered in subtract
  np.subtract(arr, avg, out=arr, casting='unsafe', where=where)


In [8]:
# List the metrics with an extreme value
outlier_imgs.aggregate_by_metric()

shape: (16, 2)
┌───────────────┬───────┐
│ metric_name   ┆ Total │
│ ---           ┆ ---   │
│ cat           ┆ u32   │
╞═══════════════╪═══════╡
│ entropy       ┆ 275   │
│ skew          ┆ 219   │
│ kurtosis      ┆ 186   │
│ brightness    ┆ 177   │
│ contrast      ┆ 168   │
│ zeros         ┆ 112   │
│ var           ┆ 90    │
│ offset_y      ┆ 60    │
│ mean          ┆ 53    │
│ std           ┆ 45    │
│ width         ┆ 43    │
│ height        ┆ 22    │
│ darkness      ┆ 20    │
│ distance_edge ┆ 18    │
│ aspect_ratio  ┆ 5     │
│ sharpness     ┆ 2     │
└───────────────┴───────┘

In [9]:
# Create the Metadata object
md = Metadata(ds)

# List the outliers by class label
outlier_imgs.aggregate_by_class(md)

shape: (21, 18)
┌─────────────┬──────────────┬────────────┬──────────┬───┬─────┬───────┬───────┬───────┐
│ class_name  ┆ aspect_ratio ┆ brightness ┆ contrast ┆ … ┆ var ┆ width ┆ zeros ┆ Total │
│ ---         ┆ ---          ┆ ---        ┆ ---      ┆   ┆ --- ┆ ---   ┆ ---   ┆ ---   │
│ cat         ┆ u32          ┆ u32        ┆ u32      ┆   ┆ u32 ┆ u32   ┆ u32   ┆ u32   │
╞═════════════╪══════════════╪════════════╪══════════╪═══╪═════╪═══════╪═══════╪═══════╡
│ person      ┆ 2            ┆ 289        ┆ 396      ┆ … ┆ 86  ┆ 31    ┆ 123   ┆ 2864  │
│ chair       ┆ 0            ┆ 144        ┆ 158      ┆ … ┆ 18  ┆ 5     ┆ 44    ┆ 1341  │
│ bottle      ┆ 3            ┆ 72         ┆ 106      ┆ … ┆ 16  ┆ 6     ┆ 22    ┆ 857   │
│ car         ┆ 0            ┆ 67         ┆ 57       ┆ … ┆ 22  ┆ 5     ┆ 33    ┆ 509   │
│ tvmonitor   ┆ 0            ┆ 71         ┆ 26       ┆ … ┆ 140 ┆ 2     ┆ 33    ┆ 472   │
│ aeroplane   ┆ 0            ┆ 128        ┆ 8        ┆ … ┆ 4   ┆ 1     ┆ 3     ┆ 412   │
│ boat        ┆ 0            ┆ 54         ┆ 15       ┆ … ┆ 4   ┆ 0     ┆ 1     ┆ 335   │
│ pottedplant ┆ 0            ┆ 41         ┆ 21       ┆ … ┆ 38  ┆ 0     ┆ 5     ┆ 309   │
│ diningtable ┆ 0            ┆ 36         ┆ 31       ┆ … ┆ 5   ┆ 0     ┆ 4     ┆ 294   │
│ bird        ┆ 0            ┆ 86         ┆ 9        ┆ … ┆ 6   ┆ 1     ┆ 11    ┆ 246   │
│ sheep       ┆ 0            ┆ 24         ┆ 2        ┆ … ┆ 3   ┆ 0     ┆ 2     ┆ 191   │
│ sofa        ┆ 0            ┆ 17         ┆ 15       ┆ … ┆ 11  ┆ 3     ┆ 8     ┆ 161   │
│ bicycle     ┆ 0            ┆ 33         ┆ 10       ┆ … ┆ 5   ┆ 8     ┆ 5     ┆ 131   │
│ motorbike   ┆ 0            ┆ 17         ┆ 18       ┆ … ┆ 6   ┆ 2     ┆ 13    ┆ 131   │
│ cat         ┆ 0            ┆ 14         ┆ 11       ┆ … ┆ 15  ┆ 4     ┆ 23    ┆ 122   │
│ dog         ┆ 0            ┆ 12         ┆ 7        ┆ … ┆ 9   ┆ 7     ┆ 18    ┆ 115   │
│ cow         ┆ 0            ┆ 6          ┆ 7        ┆ … ┆ 9   ┆ 7     ┆ 2     ┆ 88    │
│ horse       ┆ 0            ┆ 10         ┆ 13       ┆ … ┆ 3   ┆ 0     ┆ 1     ┆ 68    │
│ bus         ┆ 0            ┆ 5          ┆ 2        ┆ … ┆ 4   ┆ 2     ┆ 6     ┆ 65    │
│ train       ┆ 0            ┆ 6          ┆ 2        ┆ … ┆ 7   ┆ 2     ┆ 5     ┆ 52    │
│ Total       ┆ 5            ┆ 1132       ┆ 914      ┆ … ┆ 411 ┆ 86    ┆ 362   ┆ 8763  │
└─────────────┴──────────────┴────────────┴──────────┴───┴─────┴───────┴───────┴───────┘

In [10]:
# Plot images flagged for "entropy"
plot_sample_outlier_images_by_metric(ds, outliers, outlier_imgs, "entropy", (2, 4))

In [11]:
# Plot images flagged for "size"
plot_sample_outlier_images_by_metric(ds, outliers, outlier_imgs, "size", (2, 4))

No images flagged for metric: size


In [12]:
# Plot images flagged for "zeros"
plot_sample_outlier_images_by_metric(ds, outliers, outlier_imgs, "zeros", (2, 4))

In [13]:
# Plot images flagged for "sharpness"
plot_sample_outlier_images_by_metric(ds, outliers, outlier_imgs, "sharpness", (1, 2))

In [14]:
# Initialize the Duplicates class
dups = Duplicates()

# Find the duplicates
dups.evaluate(ds)

DuplicatesOutput(exact=[[0, 1, 2], [3, 4, 5], [6, 7, 8, 9], [10, 11, 12, 13, 14, 15], [16, 17, 18], [19, 20], [21, 22, 23, 24, 25, 26], [27, 28], [29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41], [42, 43], [44, 45], [46, 47], [48, 49], [50, 51, 52, 53], [54, 55], [56, 57], [58, 59], [60, 61, 62, 63, 64, 65], [66, 67], [68, 69, 70], [71, 72], [73, 74, 75], [76, 77], [78, 79], [80, 81, 82, 83], [84, 85, 86], [87, 88, 89, 90], [91, 92], [93, 94, 95, 96], [97, 98, 99], [100, 101, 102, 103], [104, 105, 106, 107, 108, 109], [110, 111, 112], [113, 114], [115, 116], [117, 118], [119, 120], [121, 122, 123], [124, 125], [126, 127, 128], [129, 130], [131, 132], [133, 134, 135], [136, 137, 138, 139, 140], [141, 142], [143, 144, 145], [146, 147, 148, 149, 150, 151, 152], [153, 154], [155, 156, 157], [158, 159, 160, 161, 162, 163, 164, 165], [166, 167], [168, 169, 170], [171, 172, 173, 174, 175, 176], [177, 178, 179, 180], [181, 182, 183], [184, 185], [186, 187, 188, 189, 190, 191], [192, 193], 

In [15]:
# Create exact and duplicate images

# Copy images 23 and 46 to create exact duplicates
# Copy and crop images 5 and 4376 to create near duplicates
dupes = [
    ds[23][0],
    ds[46][0],
    ds[5][0][:, 5:-5, 5:-5],
    ds[4376][0][:, :-5, 5:],
]

dupes_stats = calculate(dupes, None, ImageStats.HASH)

In [16]:
# Find the duplicates appended to the dataset
duplicates = dups.from_stats([dups.stats, dupes_stats])
print(f"exact: {duplicates.exact}")
print(f"near: {duplicates.near}")

exact: [{0: [0, 1, 2]}, {0: [3, 4, 5]}, {0: [6, 7, 8, 9]}, {0: [10, 11, 12, 13, 14, 15]}, {0: [16, 17, 18]}, {0: [19, 20]}, {0: [21, 22, 23, 24, 25, 26]}, {0: [27, 28]}, {0: [29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41]}, {0: [42, 43]}, {0: [44, 45]}, {0: [46, 47]}, {0: [48, 49]}, {0: [50, 51, 52, 53]}, {0: [54, 55]}, {0: [56, 57]}, {0: [58, 59]}, {0: [60, 61, 62, 63, 64, 65]}, {0: [66, 67]}, {0: [68, 69, 70]}, {0: [71, 72]}, {0: [73, 74, 75]}, {0: [76, 77]}, {0: [78, 79], 1: [0]}, {0: [80, 81, 82, 83]}, {0: [84, 85, 86]}, {0: [87, 88, 89, 90]}, {0: [91, 92]}, {0: [93, 94, 95, 96]}, {0: [97, 98, 99]}, {0: [100, 101, 102, 103]}, {0: [104, 105, 106, 107, 108, 109]}, {0: [110, 111, 112]}, {0: [113, 114]}, {0: [115, 116]}, {0: [117, 118]}, {0: [119, 120]}, {0: [121, 122, 123]}, {0: [124, 125]}, {0: [126, 127, 128]}, {0: [129, 130]}, {0: [131, 132]}, {0: [133, 134, 135]}, {0: [136, 137, 138, 139, 140]}, {0: [141, 142]}, {0: [143, 144, 145]}, {0: [146, 147, 148, 149, 150, 151, 152], 1